In [128]:
import numpy as np 
import pandas as pd
import torch 
import torch.nn as nn 
import matplotlib.pyplot as plt 
from os import path as path
from torch.utils.data import TensorDataset, DataLoader

In [129]:
emojies_map = pd.read_csv(path.abspath("./train_test_dataset/Mapping.csv"))
print(emojies_map.head())

train_dataset = pd.read_csv(path.abspath("./train_test_dataset/Train.csv"))
print(train_dataset.head())

   Unnamed: 0 emoticons  number
0           0         😜       0
1           1         📸       1
2           2         😍       2
3           3         😂       3
4           4         😉       4
   Unnamed: 0                                               TEXT  Label
0           0  Vacation wasted ! #vacation2017 #photobomb #ti...      0
1           1  Oh Wynwood, you’re so funny! : @user #Wynwood ...      1
2           2  Been friends since 7th grade. Look at us now w...      2
3           3  This is what it looks like when someone loves ...      3
4           4  RT @user this white family was invited to a Bl...      3


In [130]:
# now make dictionary for both "Train" and "Emojoes" 
emoji_Dict = {}

emoji_label = emojies_map["number"].values
emoji_pic = emojies_map["emoticons"].values

print(type(emoji_label), type(emoji_pic))

for x in range(len(emoji_label)): 
    emoji_Dict[int(emoji_label[x])] = emoji_pic[x]
    
print(emoji_Dict)


<class 'numpy.ndarray'> <class 'numpy.ndarray'>
{0: '😜', 1: '📸', 2: '😍', 3: '😂', 4: '😉', 5: '🎄', 6: '📷', 7: '🔥', 8: '😘', 9: '❤', 10: '😁', 11: '🇺🇸', 12: '☀', 13: '✨', 14: '💙', 15: '💕', 16: '😎', 17: '😊', 18: '💜', 19: '💯'}


In [133]:
vocabulary = set() 
train_frature = train_dataset["TEXT"].values
train_labels = train_dataset["Label"].values

max_sentence_len = 0

print(train_frature[:10])
for x in train_frature: 
    data = x.split(" ")
    data_len = len(data)
    
    max_sentence_len = data_len if data_len>=max_sentence_len else max_sentence_len
    
    # print(data)
    for y in data: 
        yy = y.replace("\n", "")
        vocabulary.add(yy)
        

['Vacation wasted ! #vacation2017 #photobomb #tired #vacationwasted #mcgar30 #miami @ Port of…\n'
 'Oh Wynwood, you’re so funny! : @user #Wynwood #Art #ItWas3AM #Flowers #Vibes @ Wynwood…\n'
 'Been friends since 7th grade. Look at us now we all following our dreams doing what we love and…\n'
 'This is what it looks like when someone loves you unconditionally oh Puppy Brother. #htx…\n'
 "RT @user this white family was invited to a Black barbecue and i've never laughed so hard in my life\n"
 "TRACK SEASON 2016, I'M READY FOR YA @ University of the Incarnate Word\n"
 'Merry Christmas you filthy little animals. Wearing a @user ugly sweater featuring Santa…\n'
 'Westenders @user #LAZzNation @ Weston, Toronto\n'
 'Maxwell heads home @ Summa Akron City Hospital\n'
 'Story On Saturday 136 Collins Ave, Miami Beach, FL 33139 Ladies Contact Me To Join Me In my…\n']


In [134]:
# the vocabulary for my dataset is 
print(vocabulary)
print(f"The Length of vocabulary is : {len(vocabulary)}")
print(f"the max sentence length is: {max_sentence_len} word")

{'attention', 'Daniel', 'Amy', 'photographer,…', 'Signature', 'Up', 'Jordan–Hare', 'hated', 'like', '#heavenwaitsforme', 'her', "life's", '#Gulfport', 'Antonio,', '2nite', 'Studios,', '#babylove', 'with…', 'Fredrick', '#bmw…', 'House…', 'tomatoes', "Carlo's", '#sleepingbeardunes', '#music', 'their', 'performance!!!', 'Bad!!!', '#TANTRICTOUR2017', 'Desert', 'Pensacola', 'Moonrise', 'Doggy', '#rushMC', 'TV', 'JACK', 'relax!', 'Naples', 'Tractor', '#2k17', '2017', 'Joywave', '#fun', 'please', 'well', 'Laughlin', '#wraloutandabout', 'fav', 'chaperoning', 'T', '#themansionproject', 'voice', 'Text', 'Far', '...#hot', 'Corps/', '#NASAAmes', 'Mesa', '#dnb', 'da', 'delicious', "here's", 'dance!', 'year', 'Born', 'Martius', 'happier', '#vegans', 'watch', 'wedding', 'Ps.', '#napask8r…', 'road', 'Olsen', 'wait…', 'dig', 'rainy', 'Chick', 'Martin', 'November', 'games', '#Thanksgiving…', 'San', 'Cruz,', 'laughs.', 'Landmarks', 'violence', 'aburrido', '#springequinox', 'kicks…', '3rd', 'Pikes', 'Also

In [136]:
vocabulary = list(vocabulary)
# print(vocabulary)

vocabulary_dict = {} 
# we hace created the "vocabulary" a python dict instead of np.array() cause searching for the index in dict takes much less time than searching of index in np.array() using np.where()
for index , x in enumerate(vocabulary): 
    vocabulary_dict[str(x)] = index
print(vocabulary_dict)

{'attention': 0, 'Daniel': 1, 'Amy': 2, 'photographer,…': 3, 'Signature': 4, 'Up': 5, 'Jordan–Hare': 6, 'hated': 7, 'like': 8, '#heavenwaitsforme': 9, 'her': 10, "life's": 11, '#Gulfport': 12, 'Antonio,': 13, '2nite': 14, 'Studios,': 15, '#babylove': 16, 'with…': 17, 'Fredrick': 18, '#bmw…': 19, 'House…': 20, 'tomatoes': 21, "Carlo's": 22, '#sleepingbeardunes': 23, '#music': 24, 'their': 25, 'performance!!!': 26, 'Bad!!!': 27, '#TANTRICTOUR2017': 28, 'Desert': 29, 'Pensacola': 30, 'Moonrise': 31, 'Doggy': 32, '#rushMC': 33, 'TV': 34, 'JACK': 35, 'relax!': 36, 'Naples': 37, 'Tractor': 38, '#2k17': 39, '2017': 40, 'Joywave': 41, '#fun': 42, 'please': 43, 'well': 44, 'Laughlin': 45, '#wraloutandabout': 46, 'fav': 47, 'chaperoning': 48, 'T': 49, '#themansionproject': 50, 'voice': 51, 'Text': 52, 'Far': 53, '...#hot': 54, 'Corps/': 55, '#NASAAmes': 56, 'Mesa': 57, '#dnb': 58, 'da': 59, 'delicious': 60, "here's": 61, 'dance!': 62, 'year': 63, 'Born': 64, 'Martius': 65, 'happier': 66, '#vegan

In [137]:
embadding_feature_arr = []

for x in train_frature: 
    data = x.split(" ")
    temp_sentence_arr = np.zeros((1, max_sentence_len))
    #print(temp_sentence_arr[0])
    
    for y in range(len(data)): 
        yy = data[y].replace("\n", "")
        # print(np.where(vocabulary == yy)[0][0])
        temp_sentence_arr[0][y] = vocabulary_dict[yy] 
    # print(temp_sentence_arr[0])
    embadding_feature_arr.append(temp_sentence_arr[0])


embadding_feature_np_arr = np.array(embadding_feature_arr)    

In [138]:
print("number of train input is: ", embadding_feature_np_arr.shape)
print("number of train output is: ", train_labels.shape)
print(embadding_feature_np_arr[0])

number of train input is:  (998, 22)
number of train output is:  (998,)
[ 994.  482. 4698.  857. 2172. 3398. 4911.  748. 3407. 4995. 4951. 2058.
    0.    0.    0.    0.    0.    0.    0.    0.    0.    0.]


In [140]:
# now convert the labels in onehot encoding
max_emoji_label_number = np.max(train_labels)
print("max emoji label number: ",max_emoji_label_number)

#so we need to formulate a 20 length of 1d numpy array to show the embadding
embadding_label_arr = []

for x in train_labels:
    temp_arr = np.zeros((1 , max_emoji_label_number+1)) #(num row , num cols)
    temp_arr[0][x] = 1
    embadding_label_arr.append(list(temp_arr[0]))

embadding_label_np_arr = np.array(embadding_label_arr)

print("label shape: ", embadding_label_np_arr.shape)
print("labels for training: ", embadding_label_np_arr)

print("features shape: ", embadding_feature_np_arr.shape)
print("features for training: ", embadding_feature_np_arr)

max emoji label number:  19
label shape:  (998, 20)
labels for training:  [[1. 0. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 ...
 [0. 1. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 1.]]
features shape:  (998, 22)
features for training:  [[ 994.  482. 4698. ...    0.    0.    0.]
 [2492. 4135.  141. ...    0.    0.    0.]
 [2483. 3673. 1565. ...    0.    0.    0.]
 ...
 [2642. 4711.  674. ...    0.    0.    0.]
 [4998. 3168. 4719. ...    0.    0.    0.]
 [4356. 4389. 1219. ...    0.    0.    0.]]


Now Work with the Glove standFord Univertsity Pretrained Model:================================

In [141]:
traned_biagram_model_path = path.abspath("./trained_biagram_model/glove.6B.50d.txt")
with open(traned_biagram_model_path , "r", encoding="utf-8") as f: 
    modelBiagram = f.readlines()

print(len(modelBiagram)) 
print(modelBiagram[0])

400000
the 0.418 0.24968 -0.41242 0.1217 0.34527 -0.044457 -0.49688 -0.17862 -0.00066023 -0.6566 0.27843 -0.14767 -0.55677 0.14658 -0.0095095 0.011658 0.10204 -0.12792 -0.8443 -0.12181 -0.016801 -0.33279 -0.1552 -0.23131 -0.19181 -1.8823 -0.76746 0.099051 -0.42125 -0.19526 4.0071 -0.18594 -0.52287 -0.31681 0.00059213 0.0074449 0.17778 -0.15897 0.012041 -0.054223 -0.29871 -0.15749 -0.34758 -0.045637 -0.44251 0.18785 0.0027849 -0.18411 -0.11514 -0.78581



In [142]:
# now we need to make a dictinary of {word: word vector} 
embeddings = {}
all_word_in_model = []
for line in modelBiagram:
    line = line.split()
    embeddings[line[0]] = np.array(line[1:], dtype = float)
    all_word_in_model.append(line[0])


In [143]:
print(len(all_word_in_model))
print(all_word_in_model)
print(len(embeddings))

400000
['the', ',', '.', 'of', 'to', 'and', 'in', 'a', '"', "'s", 'for', '-', 'that', 'on', 'is', 'was', 'said', 'with', 'he', 'as', 'it', 'by', 'at', '(', ')', 'from', 'his', "''", '``', 'an', 'be', 'has', 'are', 'have', 'but', 'were', 'not', 'this', 'who', 'they', 'had', 'i', 'which', 'will', 'their', ':', 'or', 'its', 'one', 'after', 'new', 'been', 'also', 'we', 'would', 'two', 'more', "'", 'first', 'about', 'up', 'when', 'year', 'there', 'all', '--', 'out', 'she', 'other', 'people', "n't", 'her', 'percent', 'than', 'over', 'into', 'last', 'some', 'government', 'time', '$', 'you', 'years', 'if', 'no', 'world', 'can', 'three', 'do', ';', 'president', 'only', 'state', 'million', 'could', 'us', 'most', '_', 'against', 'u.s.', 'so', 'them', 'what', 'him', 'united', 'during', 'before', 'may', 'since', 'many', 'while', 'where', 'states', 'because', 'now', 'city', 'made', 'like', 'between', 'did', 'just', 'national', 'day', 'country', 'under', 'such', 'second', 'then', 'company', 'group', 

Now we need to create a array 

In [144]:
print(len(embadding_feature_np_arr))
print(embadding_feature_np_arr.shape)

998
(998, 22)


In [145]:
pretrained_embed_dim = 50
mixDict_with_pre_trained_embadding = np.zeros((len(vocabulary_dict)+1, pretrained_embed_dim))

for word, i in vocabulary_dict.items():
    if word in embeddings:
            embed_vector = embeddings[word]
            mixDict_with_pre_trained_embadding[i] = embed_vector
    else:
        mixDict_with_pre_trained_embadding[i] = np.random.normal(scale=0.6, size=(pretrained_embed_dim,))


In [146]:
print(mixDict_with_pre_trained_embadding)

[[-0.084238    0.53053     0.12816    ...  0.5009      0.23662
   0.16071   ]
 [-1.03574753  0.9451377   0.83455142 ... -0.34836064  0.25010709
  -0.96975877]
 [ 0.37033798  0.10346337  0.37571053 ...  0.24688382 -0.68621255
   0.80232739]
 ...
 [ 0.92945256  0.66329527  0.01098805 ... -0.69688225 -0.1704955
  -0.89027826]
 [-0.28486     0.15815     0.044641   ...  0.53302    -0.15775
   0.23456   ]
 [ 0.          0.          0.         ...  0.          0.
   0.        ]]


In [164]:
embedding_matrix = torch.tensor(mixDict_with_pre_trained_embadding, dtype=torch.float32)

In [165]:
class TextClassifier(nn.Module):
    def __init__(self, embedding_matrix, num_classes):
        super(TextClassifier, self).__init__()
        self.embedding_layer = nn.Embedding.from_pretrained(embedding_matrix, freeze=False)
        self.embedding = self.embedding_layer
        self.lstm = nn.LSTM(input_size=self.embedding_layer.embedding_dim, hidden_size=128, batch_first=True)
        self.lin = nn.Linear(128, num_classes)

    def forward(self, x):
        x = self.embedding(x)  # Shape: (batch_size, sequence_length, embedding_dim)
        x, _ = self.lstm(x)    
        x = self.lin(x)         
        return x
    
model = TextClassifier(embedding_matrix , 20).to("cuda")


In [166]:
loss_fn = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.01)

In [167]:
def train(dataloader, model, loss_fn, optimizer):
  model.train()
  train_loss = 0

  for i, (X, y) in enumerate(dataloader):
    X, y = X.to("cuda"), y.to("cuda")
    y_hat = model(X)
    print(y_hat)
    
    catLoss = loss_fn(y_hat, y)
    train_loss += catLoss.item()

    optimizer.zero_grad()
    catLoss.backward()
    optimizer.step()
  
  num_batches = len(dataloader)
  train_catLoss = train_loss / num_batches
  print(f'Train RMSE: {train_catLoss**(1/2)}')

In [168]:
train_dataset = TensorDataset(torch.tensor(embadding_feature_np_arr, dtype=torch.long),
                              torch.tensor(embadding_label_np_arr, dtype=torch.long))

print(train_dataset)

In [169]:
train_dataloader = DataLoader(train_dataset, batch_size=128)

for X, y in train_dataloader:
  print(X.shape, y.shape)
  break

torch.Size([128, 22]) torch.Size([128, 20])


In [170]:
epochs = 100

for epoch in range(epochs):
  print(f"Epoch {epoch+1}:")

  train(train_dataloader, model, loss_fn, optimizer)

Epoch 1:
tensor([[[ 0.0585, -0.0183,  0.0690,  ...,  0.0628, -0.0325, -0.0292],
         [ 0.0248,  0.0244,  0.0887,  ...,  0.0865, -0.0415, -0.0231],
         [ 0.0430, -0.0616,  0.0754,  ...,  0.0267, -0.0575, -0.0018],
         ...,
         [-0.0230, -0.0629,  0.0989,  ...,  0.1223, -0.0988, -0.1027],
         [-0.0229, -0.0633,  0.0993,  ...,  0.1218, -0.0988, -0.1021],
         [-0.0228, -0.0635,  0.0995,  ...,  0.1215, -0.0988, -0.1017]],

        [[ 0.0067,  0.0216,  0.0576,  ...,  0.0469, -0.0222, -0.0479],
         [-0.0600,  0.0184,  0.0787,  ...,  0.0637,  0.0132, -0.0464],
         [-0.0115,  0.0487,  0.0855,  ...,  0.1473,  0.0262, -0.0759],
         ...,
         [-0.0239, -0.0610,  0.1004,  ...,  0.1220, -0.0984, -0.1026],
         [-0.0238, -0.0621,  0.1000,  ...,  0.1217, -0.0987, -0.1023],
         [-0.0235, -0.0628,  0.0998,  ...,  0.1214, -0.0989, -0.1019]],

        [[ 0.0131,  0.0485,  0.0532,  ...,  0.0533, -0.0481, -0.0408],
         [ 0.0171,  0.0042,  0.0415,

In [161]:
#test = ["I feel good", "I feel very bad", "lets eat dinner"]
test = ["I feel good"]

embadding_test_arr = []

for x in test: 
    data = x.split(" ")
    temp_sentence_test_arr = np.zeros((1, 34))
    
    for y in range(len(data)): 
        yy = data[y].replace("\n", "")
        temp_sentence_test_arr[0][y] = vocabulary_dict[yy] 
    embadding_test_arr.append(temp_sentence_test_arr[0])


embadding_test_np_arr = np.array([embadding_test_arr]) 
print(embadding_test_np_arr)

[[ 407. 2029. 3168.    0.    0.    0.    0.    0.    0.    0.    0.    0.
     0.    0.    0.    0.    0.    0.    0.    0.    0.    0.    0.    0.
     0.    0.    0.    0.    0.    0.    0.    0.    0.    0.]]


In [177]:
test_input = torch.tensor(embadding_test_np_arr , dtype=torch.long)
y_pred = model(test_input.to("cuda"))
y_pred = y_pred.detach().cpu()[0].numpy()
#y_pred = np.argmax(y_pred.to("cpu"), axis = 1)
print(y_pred.shape)


(34, 20)
